In [1]:
## xwrf example 
## https://ncar.github.io/esds/posts/2021/xarray-wrf-example/

import glob

import holoviews as hv
import hvplot
import hvplot.xarray
import xarray as xr
import xwrf
import geoviews as gv

from distributed import Client
from ncar_jobqueue import NCARCluster

hv.extension('bokeh')
print(xr.__version__)

2023.6.0


In [2]:
cluster = NCARCluster()
cluster.scale(10)
client = Client(cluster)
client

/glade/work/rneale/python/miniconda3/envs/neale_wrf/lib/python3.9/site-packages/dask_jobqueue/core.py:255: FutureWarning: job_extra has been renamed to job_extra_directives. You are still using it (even if only set to []; please also check config files). If you did not set job_extra_directives yet, job_extra will be respected for now, but it will be removed in a future release. If you already set job_extra_directives, job_extra is ignored and you can remove it.
  warnings.warn(warn, FutureWarning)
/glade/work/rneale/python/miniconda3/envs/neale_wrf/lib/python3.9/site-packages/dask_jobqueue/core.py:274: FutureWarning: env_extra has been renamed to job_script_prologue. You are still using it (even if only set to []; please also check config files). If you did not set job_script_prologue yet, env_extra will be respected for now, but it will be removed in a future release. If you already set job_script_prologue, env_extra is ignored and you can remove it.
  warnings.warn(warn, FutureWarnin

<Client: 'tcp://10.148.0.5:34239' processes=0 threads=0, memory=0 B>

In [3]:
#files = sorted(glob.glob('/glade/scratch/rneale/SAAG/wrf2d_d01_daily_tot_201007*.nc'))
files = sorted(glob.glob('/glade/scratch/rneale/SAAG/201506_PREC_ACC_NC_SouthAmerica.nc'))

In [4]:
file_subset = files[-80:]

In [5]:
print(files[0])
wrf_ds = xr.open_dataset(files[0])
print(wrf_ds)


/glade/scratch/rneale/SAAG/201506_PREC_ACC_NC_SouthAmerica.nc
<xarray.Dataset>
Dimensions:      (rlat: 2027, rlon: 1471, time: 720)
Coordinates:
    lat          (rlat, rlon) float32 ...
    lon          (rlat, rlon) float32 ...
  * time         (time) datetime64[ns] 2015-06-01 ... 2015-06-30T23:00:00
Dimensions without coordinates: rlat, rlon
Data variables:
    PREC_ACC_NC  (time, rlat, rlon) float32 ...


In [6]:
for var in wrf_ds:
    try:
        print(f'variable: {var}, description: {wrf_ds[var].description}')
    except:
        pass
    

In [7]:
%%time
variables = ["PREC_ACC_NC"]


def preprocess(ds):
    return ds[variables]


ds = xr.open_mfdataset(
    file_subset,
    engine="xwrf",
    parallel=False,
    combine="nested",
    preprocess=preprocess
)

CPU times: user 13.7 ms, sys: 12.6 ms, total: 26.3 ms
Wall time: 25.7 ms


/glade/work/rneale/python/miniconda3/envs/neale_wrf/lib/python3.9/site-packages/xwrf/io_plugin.py:115: UserWarning: Failed to parse time coordinate: time
  return clean(dataset)


In [8]:
ds

<xarray.Dataset>
Dimensions:      (time: 720, rlat: 2027, rlon: 1471)
Coordinates:
    lat          (rlat, rlon) float32 dask.array<chunksize=(2027, 1471), meta=np.ndarray>
    lon          (rlat, rlon) float32 dask.array<chunksize=(2027, 1471), meta=np.ndarray>
  * time         (time) datetime64[ns] 2015-06-01 ... 2015-06-30T23:00:00
Dimensions without coordinates: rlat, rlon
Data variables:
    PREC_ACC_NC  (time, rlat, rlon) float32 dask.array<chunksize=(720, 2027, 1471), meta=np.ndarray>

In [9]:
#ds = ds.isel(num_metgrid_levels=range(1, 21))


In [10]:
#ds_to_plot = ds.rename({'num_metgrid_levels': 'plev'})
ds_to_plot = ds


In [11]:
#plevs = ds_to_plot.PRES.isel(south_north=0, west_east=0).values[0, :]
#ds_to_plot['plev'] = plevs / 100
#ds_to_plot['plev'].attrs['units'] = 'hPa'


In [12]:
ds_to_plot['time'] = ds.time
ds_to_plot.time
#ds_to_plot['PREC_ACC_NC'][300,:,:].plot()

<xarray.DataArray 'time' (time: 720)>
array(['2015-06-01T00:00:00.000000000', '2015-06-01T01:00:00.000000000',
       '2015-06-01T02:00:00.000000000', ..., '2015-06-30T21:00:00.000000000',
       '2015-06-30T22:00:00.000000000', '2015-06-30T23:00:00.000000000'],
      dtype='datetime64[ns]')
Coordinates:
  * time     (time) datetime64[ns] 2015-06-01 ... 2015-06-30T23:00:00
Attributes:
    standard_name:  time
    long_name:      time

In [13]:
#ds_to_plot.PREC_ACC_NC.plot
plot = ds_to_plot.hvplot.quadmesh(
    x='lon',
    y='lat',
    z='PREC_ACC_NC',
    groupby='time',
    widget_location='bottom',
    rasterize=True,
    coastline=True,
    clim=(0., 10),
    cmap='GnBu',
    width=800,height=600,
    project=True,
    dynamic=True,
)
plot


Column
    [0] HoloViews(DynamicMap, height=600, sizing_mode='fixed', widget_location='bottom', width=800)
    [1] WidgetBox(align=('center', 'end'))
        [0] DiscreteSlider(margin=(20, 20, 20, 20), name='time', options=OrderedDict([('2015-06-01 ...]), value=numpy.datetime64('2015-06-..., width=250)